In [1]:
import sys 
sys.path.append('..')
from cox.utils import Parameters
from cox.store import Store
from cox.readers import CollectionReader
from sklearn.metrics import mean_squared_error
from sklearn.linear_model import LinearRegression
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import math
import numpy as np
import torch as ch
from torch import Tensor
from torch.distributions.normal import Normal
from torch.distributions.multivariate_normal import MultivariateNormal
from torch.distributions import Uniform
from torch.utils.data import DataLoader
from delphi.stats.truncated_regression import truncated_regression
from delphi.utils.datasets import TruncatedRegressionDataset
from delphi.oracle import Left, Interval
import datetime

In [2]:
STORE_PATH = '/home/pstefanou/Uniform2'
STORE_TABLE_NAME = 'uniform'

store = Store(STORE_PATH)

store.add_table(STORE_TABLE_NAME, { 
    'known_param_mse': float,
    'unknown_param_mse': float, 
    'unknown_var_mse': float,
    'ols_param_mse': float,
    'alpha': float, 
    'var': float, 
})

Logging in: /home/pstefanou/Uniform2/090a18a7-3237-49eb-85a2-f8514ff16efe


In [3]:
# regression parameters
NUM_SAMPLES, DIMS = 10000, 10
PREDICATE = Left(Tensor([1.0]))
LOWER, UPPER = -1, 1

In [4]:
# perform each experiment a total of 10 times
for iter_ in range(10):        
    for var in range(1, 10):
        # generate random uniform weights
        W = Uniform(LOWER, UPPER).sample(ch.Size([DIMS, 1]))
        W0 = Uniform(LOWER, UPPER).sample(ch.Size([1, 1]))

        # generate data
        X = Uniform(0, 1).sample(ch.Size([NUM_SAMPLES, DIMS]))
        y = X.mm(W) + W0 + Normal(ch.zeros(1), ch.sqrt(Tensor([var]))).sample(ch.Size([NUM_SAMPLES]))
        # truncate
        indices = PREDICATE(y).nonzero(as_tuple=False).flatten()
        y_trunc, x_trunc = y[indices], X[indices]

        # empirical linear regression
        reg = LinearRegression() 
        reg.fit(x_trunc, y_trunc)
        emp_var = ch.var(ch.from_numpy(reg.predict(x_trunc)) - y_trunc, dim=0).unsqueeze(0)

        # experiment parameters
        args = Parameters({ 
            'alpha': Tensor([y_trunc.size(0)/NUM_SAMPLES]), 
            'phi': PREDICATE, 
            'epochs': 10,
            'num_workers': 1, 
            'batch_size': 100,
            'bias': True,
            'num_samples': 100,
            'clamp': True, 
            'radius': 5.0, 
            'var_lr': 1e-2,
            'var': emp_var,
            'lr': 1e-1,
            'shuffle': True, 
            'tol': 5e-2,
        })


        # truncated linear regression with known noise variance
        data = TruncatedRegressionDataset(x_trunc, y_trunc, bias=args.bias, unknown=False)
        S = DataLoader(data, batch_size=args.batch_size, num_workers=args.num_workers, shuffle=args.shuffle)
        trunc_reg = truncated_regression(phi=args.phi, alpha=args.alpha, epochs=args.epochs, lr=args.lr, num_samples=args.num_samples, var=args.var, tol=args.tol)
        results = trunc_reg.fit(S)
        w_, w0_ = results.weight.detach().cpu(), results.bias.detach().cpu()

        # truncated linear regression with unknown noise variance
        data = TruncatedRegressionDataset(x_trunc, y_trunc, bias=args.bias, unknown=True)
        S = DataLoader(data, batch_size=args.batch_size, num_workers=args.num_workers, shuffle=args.shuffle)
        trunc_reg = truncated_regression(phi=args.phi, alpha=args.alpha, epochs=args.epochs, var_lr=args.var_lr, lr=args.lr, num_samples=args.num_samples, tol=args.tol)

        results = trunc_reg.fit(S)
        var_ = results.lambda_.inverse().detach().cpu()
        w, w0 = (results.v.detach()*var_).cpu(), (results.bias.detach()*var_).cpu()

        # parameters 
        real_params = ch.cat([W, W0])
        ols_params = ch.cat([data.w, data.w0.unsqueeze(0)])
        unknown_params = ch.cat([w, w0])
        known_params = ch.cat([w_.t(), w0_.unsqueeze(0)])
        
        # metrics
        unknown_param_mse = mean_squared_error(unknown_params, real_params)
        unknown_var_mse = mean_squared_error(var_, Tensor([var]))
        ols_param_mse = mean_squared_error(ols_params, real_params)
        known_param_mse = mean_squared_error(known_params, real_params)


        store[STORE_TABLE_NAME].append_row({ 
            'known_param_mse': known_param_mse,
            'unknown_param_mse': unknown_param_mse,
            'unknown_var_mse': unknown_var_mse,
            'ols_param_mse': ols_param_mse,
            'alpha': float(args.alpha.flatten()),
            'var': float(var), 
        })

# close current store
store.close()

Epoch:1 | Score tensor([0.0856, 0.0908, 0.0886, 0.1130, 0.1016, 0.1098, 0.1158, 0.1389, 0.1017,
        0.0763, 0.1956]) 
Epoch:1 | Score tensor([0.0856, 0.0908, 0.0886, 0.1130, 0.1016, 0.1098, 0.1158, 0.1389, 0.1017,
        0.0763, 0.1956]) 
Epoch:1 | Score tensor([0.0588, 0.0637, 0.0704, 0.0885, 0.0626, 0.0721, 0.0755, 0.1041, 0.0635,
        0.0388, 0.1313]) 
Epoch:1 | Score tensor([0.0588, 0.0637, 0.0704, 0.0885, 0.0626, 0.0721, 0.0755, 0.1041, 0.0635,
        0.0388, 0.1313]) 
Epoch:1 | Score tensor([0.0831, 0.0917, 0.0963, 0.0947, 0.0933, 0.0913, 0.0967, 0.1126, 0.0900,
        0.0690, 0.1799]) 
Epoch:1 | Score tensor([0.0831, 0.0917, 0.0963, 0.0947, 0.0933, 0.0913, 0.0967, 0.1126, 0.0900,
        0.0690, 0.1799]) 
Epoch:1 | Score tensor([0.0765, 0.0881, 0.0881, 0.0864, 0.0857, 0.0796, 0.0820, 0.1033, 0.0855,
        0.0671, 0.1653]) 
Epoch:1 | Score tensor([0.0765, 0.0881, 0.0881, 0.0864, 0.0857, 0.0796, 0.0820, 0.1033, 0.0855,
        0.0671, 0.1653]) 
Epoch:1 | Score tensor([

Epoch:1 | Score tensor([0.0582, 0.0530, 0.0538, 0.0569, 0.0556, 0.0534, 0.0613, 0.0649, 0.0588,
        0.0605, 0.1179]) 
Epoch:1 | Score tensor([0.0591, 0.0546, 0.0560, 0.0591, 0.0580, 0.0546, 0.0632, 0.0661, 0.0597,
        0.0620, 0.1215]) 
Epoch:1 | Score tensor([0.0591, 0.0546, 0.0560, 0.0591, 0.0580, 0.0546, 0.0632, 0.0661, 0.0597,
        0.0620, 0.1215]) 
Epoch:1 | Score tensor([0.0616, 0.0581, 0.0588, 0.0617, 0.0598, 0.0568, 0.0652, 0.0679, 0.0623,
        0.0643, 0.1265]) 
Epoch:1 | Score tensor([0.0616, 0.0581, 0.0588, 0.0617, 0.0598, 0.0568, 0.0652, 0.0679, 0.0623,
        0.0643, 0.1265]) 
Epoch:1 | Score tensor([0.0616, 0.0581, 0.0588, 0.0617, 0.0598, 0.0568, 0.0652, 0.0679, 0.0623,
        0.0643, 0.1265]) 
Epoch:1 | Score tensor([0.0615, 0.0580, 0.0575, 0.0595, 0.0579, 0.0559, 0.0640, 0.0666, 0.0609,
        0.0634, 0.1242]) 
Epoch:1 | Score tensor([0.0615, 0.0580, 0.0575, 0.0595, 0.0579, 0.0559, 0.0640, 0.0666, 0.0609,
        0.0634, 0.1242]) 
Epoch:1 | Score tensor([

Epoch:1 | Score tensor([0.0563, 0.0475, 0.0478, 0.0522, 0.0475, 0.0482, 0.0574, 0.0574, 0.0515,
        0.0534, 0.1057]) 
Epoch:1 | Score tensor([0.0562, 0.0473, 0.0473, 0.0521, 0.0472, 0.0481, 0.0570, 0.0571, 0.0510,
        0.0526, 0.1051]) 
Epoch:1 | Score tensor([0.0562, 0.0473, 0.0473, 0.0521, 0.0472, 0.0481, 0.0570, 0.0571, 0.0510,
        0.0526, 0.1051]) 
Epoch:1 | Score tensor([0.0557, 0.0468, 0.0472, 0.0524, 0.0474, 0.0486, 0.0575, 0.0569, 0.0513,
        0.0523, 0.1052]) 
Epoch:1 | Score tensor([0.0557, 0.0468, 0.0472, 0.0524, 0.0474, 0.0486, 0.0575, 0.0569, 0.0513,
        0.0523, 0.1052]) 
Epoch:1 | Score tensor([0.0550, 0.0466, 0.0463, 0.0515, 0.0467, 0.0484, 0.0563, 0.0564, 0.0513,
        0.0519, 0.1043]) 
Epoch:1 | Score tensor([0.0550, 0.0466, 0.0463, 0.0515, 0.0467, 0.0484, 0.0563, 0.0564, 0.0513,
        0.0519, 0.1043]) 
Epoch:1 | Score tensor([0.0541, 0.0462, 0.0458, 0.0512, 0.0461, 0.0480, 0.0558, 0.0559, 0.0505,
        0.0513, 0.1030]) 
Epoch:1 | Score tensor([

 | Loss 0.2188 ||:   0%|          | 0/74 [00:00<?, ?it/s]/home/pstefanou/env/lib/python3.6/site-packages/torch/autograd/__init__.py:132: UserWarning: grad and param do not obey the gradient layout contract. This is not an error, but may impair performance.
grad.sizes() = [10, 1], strides() = [1, 10]
param.sizes() = [10, 1], strides() = [1, 1] (Triggered internally at  /pytorch/torch/csrc/autograd/functions/accumulate_grad.h:170.)
  allow_unreachable=True)  # allow_unreachable flag
Epoch:1 | Score tensor([ 0.0133,  0.0025,  0.0070,  0.0176,  0.0286,  0.0217,  0.0066,  0.0473,
         0.0254,  0.0363,  0.0498, -0.0256]) 
Epoch:1 | Score tensor([ 0.0133,  0.0025,  0.0070,  0.0176,  0.0286,  0.0217,  0.0066,  0.0473,
         0.0254,  0.0363,  0.0498, -0.0256]) 
Epoch:1 | Score tensor([ 0.0133,  0.0025,  0.0070,  0.0176,  0.0286,  0.0217,  0.0066,  0.0473,
         0.0254,  0.0363,  0.0498, -0.0256]) 
 | Loss 0.2881 ||:   1%|▏         | 1/74 [00:00<00:05, 14.30it/s]
Epoch:1 | Score tensor

Epoch:1 | Score tensor([0.0812, 0.0779, 0.0850, 0.0811, 0.0857, 0.0849, 0.0876, 0.0845, 0.0838,
        0.0865, 0.1719]) 
Epoch:1 | Score tensor([0.0798, 0.0780, 0.0832, 0.0799, 0.0864, 0.0823, 0.0879, 0.0833, 0.0833,
        0.0871, 0.1697]) 
Epoch:1 | Score tensor([0.0798, 0.0780, 0.0832, 0.0799, 0.0864, 0.0823, 0.0879, 0.0833, 0.0833,
        0.0871, 0.1697]) 
Epoch:1 | Score tensor([0.0843, 0.0808, 0.0877, 0.0845, 0.0903, 0.0869, 0.0912, 0.0887, 0.0871,
        0.0911, 0.1772]) 
Epoch:1 | Score tensor([0.0843, 0.0808, 0.0877, 0.0845, 0.0903, 0.0869, 0.0912, 0.0887, 0.0871,
        0.0911, 0.1772]) 
Epoch:1 | Score tensor([0.0827, 0.0785, 0.0849, 0.0823, 0.0880, 0.0842, 0.0878, 0.0869, 0.0847,
        0.0885, 0.1721]) 
Epoch:1 | Score tensor([0.0827, 0.0785, 0.0849, 0.0823, 0.0880, 0.0842, 0.0878, 0.0869, 0.0847,
        0.0885, 0.1721]) 
Epoch:1 | Score tensor([0.0823, 0.0771, 0.0841, 0.0799, 0.0857, 0.0846, 0.0869, 0.0862, 0.0826,
        0.0890, 0.1697]) 
Epoch:1 | Score tensor([

...

Epoch:3 | Score tensor([ 0.0119,  0.0039,  0.0015, -0.0152,  0.0102,  0.0110,  0.0262, -0.0073,
        -0.0131,  0.0012,  0.0305,  0.4167]) 
Epoch:3 | Score tensor([ 0.0119,  0.0039,  0.0015, -0.0152,  0.0102,  0.0110,  0.0262, -0.0073,
        -0.0131,  0.0012,  0.0305,  0.4167]) 
Epoch:3 | Score tensor([ 0.0119,  0.0039,  0.0015, -0.0152,  0.0102,  0.0110,  0.0262, -0.0073,
        -0.0131,  0.0012,  0.0305,  0.4167]) 
Epoch:3 | Score tensor([ 0.0164,  0.0078,  0.0009, -0.0054,  0.0103,  0.0131,  0.0253, -0.0037,
        -0.0070,  0.0030,  0.0341,  0.3889]) 
Epoch:3 | Score tensor([ 0.0164,  0.0078,  0.0009, -0.0054,  0.0103,  0.0131,  0.0253, -0.0037,
        -0.0070,  0.0030,  0.0341,  0.3889]) 
Epoch:3 | Score tensor([ 1.1571e-02,  5.1669e-03,  2.8475e-03, -1.6605e-04,  1.7874e-02,
         1.0037e-02,  2.0067e-02, -6.5599e-03,  2.9619e-03,  1.9750e-03,
         4.1174e-02,  3.5119e-01]) 
Epoch:3 | Score tensor([ 1.1571e-02,  5.1669e-03,  2.8475e-03, -1.6605e-04,  1.7874e-02,
   

Epoch:4 | Score tensor([-0.0053, -0.0420, -0.0615, -0.0672, -0.0912, -0.0661, -0.0010, -0.0486,
        -0.1393, -0.0036, -0.0683,  0.8187]) 
Epoch:4 | Score tensor([ 0.0974,  0.0112,  0.0721,  0.0294,  0.0678,  0.0198,  0.0731,  0.0010,
         0.0277,  0.0815,  0.1199, -0.0789]) 
Epoch:4 | Score tensor([ 0.0974,  0.0112,  0.0721,  0.0294,  0.0678,  0.0198,  0.0731,  0.0010,
         0.0277,  0.0815,  0.1199, -0.0789]) 
Epoch:4 | Score tensor([ 0.1470,  0.1065,  0.0911,  0.0356,  0.1124,  0.0441,  0.0682,  0.0140,
         0.0528,  0.1066,  0.2056, -0.4409]) 
Epoch:4 | Score tensor([ 0.1470,  0.1065,  0.0911,  0.0356,  0.1124,  0.0441,  0.0682,  0.0140,
         0.0528,  0.1066,  0.2056, -0.4409]) 
Epoch:4 | Score tensor([ 0.0632,  0.0256, -0.0097, -0.0447,  0.0508,  0.0297,  0.0034, -0.0491,
        -0.0050,  0.0151,  0.0901,  0.0168]) 
Epoch:4 | Score tensor([ 0.0632,  0.0256, -0.0097, -0.0447,  0.0508,  0.0297,  0.0034, -0.0491,
        -0.0050,  0.0151,  0.0901,  0.0168]) 
Epoch:

Epoch:4 | Score tensor([ 0.0182, -0.0055,  0.0022, -0.0061,  0.0103,  0.0161, -0.0051,  0.0056,
         0.0088,  0.0162,  0.0506,  0.0865]) 
Epoch:4 | Score tensor([ 0.0182, -0.0055,  0.0022, -0.0061,  0.0103,  0.0161, -0.0051,  0.0056,
         0.0088,  0.0162,  0.0506,  0.0865]) 
Epoch:4 | Score tensor([ 0.0223, -0.0005,  0.0036, -0.0036,  0.0143,  0.0172,  0.0003,  0.0094,
         0.0117,  0.0187,  0.0597,  0.0468]) 
Epoch:4 | Score tensor([ 0.0223, -0.0005,  0.0036, -0.0036,  0.0143,  0.0172,  0.0003,  0.0094,
         0.0117,  0.0187,  0.0597,  0.0468]) 
Epoch:4 | Score tensor([ 0.0216, -0.0014,  0.0017, -0.0056,  0.0109,  0.0164, -0.0004,  0.0076,
         0.0089,  0.0186,  0.0552,  0.0603]) 
Epoch:4 | Score tensor([ 0.0216, -0.0014,  0.0017, -0.0056,  0.0109,  0.0164, -0.0004,  0.0076,
         0.0089,  0.0186,  0.0552,  0.0603]) 
Epoch:4 | Score tensor([ 0.0232, -0.0012,  0.0018, -0.0028,  0.0100,  0.0162, -0.0015,  0.0100,
         0.0067,  0.0186,  0.0539,  0.0784]) 
Epoch:

Epoch:5 | Score tensor([-0.0169,  0.0008, -0.0264, -0.0294,  0.0014, -0.0376, -0.0131, -0.0125,
        -0.0406, -0.0037, -0.0183,  0.3278]) 
Epoch:5 | Score tensor([-0.0007,  0.0185, -0.0067, -0.0178,  0.0096, -0.0264, -0.0058,  0.0042,
        -0.0200,  0.0038,  0.0092,  0.2105]) 
Epoch:5 | Score tensor([-0.0007,  0.0185, -0.0067, -0.0178,  0.0096, -0.0264, -0.0058,  0.0042,
        -0.0200,  0.0038,  0.0092,  0.2105]) 
Epoch:5 | Score tensor([-0.0093,  0.0193, -0.0075, -0.0184,  0.0083, -0.0268, -0.0086, -0.0032,
        -0.0128,  0.0065,  0.0091,  0.2239]) 
Epoch:5 | Score tensor([-0.0093,  0.0193, -0.0075, -0.0184,  0.0083, -0.0268, -0.0086, -0.0032,
        -0.0128,  0.0065,  0.0091,  0.2239]) 
Epoch:5 | Score tensor([-0.0123,  0.0136, -0.0132, -0.0217,  0.0119, -0.0245, -0.0127, -0.0074,
        -0.0132,  0.0054,  0.0078,  0.2271]) 
Epoch:5 | Score tensor([-0.0123,  0.0136, -0.0132, -0.0217,  0.0119, -0.0245, -0.0127, -0.0074,
        -0.0132,  0.0054,  0.0078,  0.2271]) 
Epoch:

Epoch:6 | Score tensor([ 0.0596,  0.1408,  0.1898,  0.0976,  0.0863,  0.0570,  0.1017,  0.1297,
         0.0949,  0.0650,  0.2409, -0.7261]) 
Epoch:6 | Score tensor([ 0.0538,  0.1426,  0.1740,  0.0864,  0.0870,  0.0558,  0.0776,  0.0970,
         0.0860,  0.0950,  0.2195, -0.6320]) 
Epoch:6 | Score tensor([ 0.0538,  0.1426,  0.1740,  0.0864,  0.0870,  0.0558,  0.0776,  0.0970,
         0.0860,  0.0950,  0.2195, -0.6320]) 
Epoch:6 | Score tensor([ 0.0490,  0.1367,  0.1765,  0.1064,  0.1036,  0.0703,  0.0978,  0.0974,
         0.0783,  0.0944,  0.2320, -0.7616]) 
Epoch:6 | Score tensor([ 0.0490,  0.1367,  0.1765,  0.1064,  0.1036,  0.0703,  0.0978,  0.0974,
         0.0783,  0.0944,  0.2320, -0.7616]) 
Epoch:6 | Score tensor([ 0.0146,  0.0892,  0.1329,  0.0831,  0.0862,  0.0241,  0.0733,  0.0669,
         0.0633,  0.0538,  0.1626, -0.4128]) 
Epoch:6 | Score tensor([ 0.0146,  0.0892,  0.1329,  0.0831,  0.0862,  0.0241,  0.0733,  0.0669,
         0.0633,  0.0538,  0.1626, -0.4128]) 
Epoch:

In [9]:
reader = CollectionReader(STORE_PATH)
results = reader.df(STORE_TABLE_NAME)
results.head()

  0%|          | 0/1 [00:00<?, ?it/s]


OSError: HDF5 error back trace

  File "H5F.c", line 509, in H5Fopen
    unable to open file
  File "H5Fint.c", line 1400, in H5F__open
    unable to open file
  File "H5Fint.c", line 1615, in H5F_open
    unable to lock the file
  File "H5FD.c", line 1640, in H5FD_lock
    driver lock request failed
  File "H5FDsec2.c", line 941, in H5FD_sec2_lock
    unable to lock file, errno = 11, error message = 'Resource temporarily unavailable'

End of HDF5 error back trace

Unable to open/create file '/home/pstefanou/Uniform2/090a18a7-3237-49eb-85a2-f8514ff16efe/store.h5'

In [6]:
known, unknown, ols = results[['known_param_mse', 'var']], results[['unknown_param_mse', 'var']], results[['ols_param_mse', 'var']]

TypeError: 'LinearUnknownVariance' object is not subscriptable

In [7]:
# plot results for regression parameter MSE
sns.lineplot(data=unknown, x='var', y='unknown_param_mse', label='unknown', color='blue')
sns.lineplot(data=known, x='var', y='known_param_mse', label='known', color='purple')
ax = sns.lineplot(data=ols, x='var', y='ols_param_mse', label='ols', color='red')
ax.set(xlabel='Noise Variance', ylabel='Squared Error')
plt.show()
# close reader
reader.close()

NameError: name 'unknown' is not defined

In [21]:
store.close()

In [20]:
print("hi")

hi


In [8]:
store.close()

In [21]:
reader = CollectionReader(STORE_PATH)

  0%|          | 0/3 [00:00<?, ?it/s]


OSError: HDF5 error back trace

  File "H5F.c", line 509, in H5Fopen
    unable to open file
  File "H5Fint.c", line 1400, in H5F__open
    unable to open file
  File "H5Fint.c", line 1615, in H5F_open
    unable to lock the file
  File "H5FD.c", line 1640, in H5FD_lock
    driver lock request failed
  File "H5FDsec2.c", line 941, in H5FD_sec2_lock
    unable to lock file, errno = 11, error message = 'Resource temporarily unavailable'

End of HDF5 error back trace

Unable to open/create file '/home/pstefanou/Uniform2/4ddbd332-885b-4224-ac3d-7678e5623eda/store.h5'

In [22]:
Store('/home/pstefanou/Uniform2', '4ddbd332-885b-4224-ac3d-7678e5623eda')

HDF5ExtError: HDF5 error back trace

  File "H5F.c", line 509, in H5Fopen
    unable to open file
  File "H5Fint.c", line 1400, in H5F__open
    unable to open file
  File "H5Fint.c", line 1615, in H5F_open
    unable to lock the file
  File "H5FD.c", line 1640, in H5FD_lock
    driver lock request failed
  File "H5FDsec2.c", line 941, in H5FD_sec2_lock
    unable to lock file, errno = 11, error message = 'Resource temporarily unavailable'

End of HDF5 error back trace

Unable to open/create file '/home/pstefanou/Uniform2/4ddbd332-885b-4224-ac3d-7678e5623eda/store.h5'